In [170]:
import os
import datetime
import warnings
import polars as pl
import pandas as pd
import altair as alt

from src.najdi_rok import najdi_rok
from src.pocet_stran import pocet_stran
from src.bez_bordelu import bez_bordelu
from src.alt_friendly import alt_friendly
from src.hezke_jmeno import hezke_jmeno
from src.kristi_promin import kristi_promin
from src.zjisti_vazbu import zjisti_vazbu

pl.Config(tbl_rows=100)
alt.data_transformers.disable_max_rows()
alt.themes.register('irozhlas', kristi_promin)
alt.themes.enable('irozhlas')
warnings.filterwarnings('ignore')

In [171]:
df = pl.read_parquet(os.path.join("data/cnb_sloupce","100.parquet"))
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","leader.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","008.parquet")), left_on="001", right_on="001", how="left")
df = df.to_pandas()
df = df[df["leader"].str[6].isin(["a", "t"])]
df = df[~df["leader"].str[7].isin(["b", "i", "s", " "])]
df = df[(df["008"].str[15:17] == "xr") & (df["008"].str[35:38] == "cze")]
df = pl.from_pandas(df)
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","020.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","022.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","245.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","300.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","655.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","700.parquet")), left_on="001", right_on="001", how="left")
df = df.explode("022_a").filter(pl.col("022_a").is_null())
df = df.with_columns(pl.col('008').map_elements(najdi_rok, return_dtype=int).alias('rok'))
df = df.with_columns(pl.col('300_a').map_elements(pocet_stran, return_dtype=int).alias('stran'))
df = df.with_columns(pl.col('245_a').map_elements(bez_bordelu, return_dtype=str))
df = df.explode("020_q").with_columns(pl.col("020_q").map_elements(zjisti_vazbu, return_dtype=str).alias('vazba'))
df = df.explode('245_p').with_columns(pl.col('245_p').map_elements(bez_bordelu, return_dtype=str))
print(len(df))
df = df.filter(pl.col("rok") >= 1800)

df = df.filter((~pl.col("245_h").str.contains("grafika")) | pl.col("245_h").is_null()).unique(subset=["008","100_a","245_a","245_p"], keep="first")
print(len(df))

794838
705250


In [172]:
df = df.filter(pl.col("rok") <= 2024)

In [173]:
bestsellery = pd.read_json(os.path.join("data","sckn_zebricky.json"))
bestsellery = pl.from_pandas(bestsellery)
bestsellery
isbn_bestselleru = set(bestsellery.select(pl.col("sckn_isbn")).to_series().to_list())
df_isbn = df.explode("020_a").drop_nulls(subset=['020_a']).with_columns(pl.col("020_a").map_elements(lambda x: x.replace('-','')).alias("isbn"))

## Vazby

In [175]:
def podil_vazeb(frejm):
    vazby = frejm.filter(pl.col("vazba") == 'brožovaná').group_by("rok").len().sort(by="rok").rename({"len":"brožovaná"})
    vazby = vazby.join(df.filter(pl.col("vazba").is_in(['brožovaná','pevná'])).group_by("rok").len().sort(by="rok").rename({"len":"jakákoliv"}), left_on="rok", right_on="rok", how="left")
    vazby = vazby.join(df.group_by("rok").len().sort(by="rok").rename({"len":"vše"}), left_on="rok", right_on="rok", how="left")
    vazby = vazby.with_columns((pl.col("brožovaná") / pl.col("jakákoliv")).alias("podíl"))
    vazby = vazby.with_columns((pl.col("jakákoliv") / pl.col("vše")).alias("vyplněnost"))
    return vazby

In [176]:
podil_vazeb(df)

shape: (224, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 1801 ┆ 8         ┆ 11        ┆ 12    ┆ 0.727273 ┆ 0.916667   │
│ 1802 ┆ 4         ┆ 10        ┆ 12    ┆ 0.4      ┆ 0.833333   │
│ 1803 ┆ 7         ┆ 11        ┆ 16    ┆ 0.636364 ┆ 0.6875     │
│ 1804 ┆ 8         ┆ 12        ┆ 17    ┆ 0.666667 ┆ 0.705882   │
│ 1805 ┆ 9         ┆ 14        ┆ 16    ┆ 0.642857 ┆ 0.875      │
│ 1806 ┆ 4         ┆ 7         ┆ 9     ┆ 0.571429 ┆ 0.777778   │
│ 1807 ┆ 8         ┆ 13        ┆ 18    ┆ 0.615385 ┆ 0.722222   │
│ 1808 ┆ 7         ┆ 9         ┆ 14    ┆ 0.777778 ┆ 0.642857   │
│ 1809 ┆ 6         ┆ 12        ┆ 15    ┆ 0.5      ┆ 0.8        │
│ 1810 ┆ 11        ┆ 12        ┆ 17    ┆ 0.916667 ┆ 0.705882   │
│ 1811 ┆ 6         ┆ 7         ┆ 10    ┆ 0.857143 ┆ 0.7        │
│ 1812 ┆ 16        ┆ 19        ┆ 21    ┆ 0.842105 ┆ 0.904762   │
│ 1813 ┆ 10        ┆ 14        ┆ 16    ┆ 0.714286 ┆ 0.875      │
│ 1814 ┆ 13        ┆ 18        ┆ 23    ┆ 0.722222 ┆ 0.782609   │
│ 1815 ┆ 16        ┆ 18        ┆ 21    ┆ 0.888889 ┆ 0.857143   │
│ 1816 ┆ 13        ┆ 17        ┆ 22    ┆ 0.764706 ┆ 0.772727   │
│ 1817 ┆ 11        ┆ 18        ┆ 21    ┆ 0.611111 ┆ 0.857143   │
│ 1818 ┆ 23        ┆ 36        ┆ 39    ┆ 0.638889 ┆ 0.923077   │
│ 1819 ┆ 25        ┆ 35        ┆ 41    ┆ 0.714286 ┆ 0.853659   │
│ 1820 ┆ 19        ┆ 36        ┆ 41    ┆ 0.527778 ┆ 0.878049   │
│ 1821 ┆ 37        ┆ 46        ┆ 54    ┆ 0.804348 ┆ 0.851852   │
│ 1822 ┆ 29        ┆ 34        ┆ 42    ┆ 0.852941 ┆ 0.809524   │
│ 1823 ┆ 33        ┆ 40        ┆ 46    ┆ 0.825    ┆ 0.869565   │
│ 1824 ┆ 32        ┆ 42        ┆ 51    ┆ 0.761905 ┆ 0.823529   │
│ 1825 ┆ 35        ┆ 48        ┆ 55    ┆ 0.729167 ┆ 0.872727   │
│ 1826 ┆ 28        ┆ 32        ┆ 36    ┆ 0.875    ┆ 0.888889   │
│ 1827 ┆ 36        ┆ 48        ┆ 55    ┆ 0.75     ┆ 0.872727   │
│ 1828 ┆ 25        ┆ 41        ┆ 48    ┆ 0.609756 ┆ 0.854167   │
│ 1829 ┆ 21        ┆ 32        ┆ 36    ┆ 0.65625  ┆ 0.888889   │
│ 1830 ┆ 33        ┆ 44        ┆ 56    ┆ 0.75     ┆ 0.785714   │
│ 1831 ┆ 31        ┆ 42        ┆ 49    ┆ 0.738095 ┆ 0.857143   │
│ 1832 ┆ 26        ┆ 32        ┆ 38    ┆ 0.8125   ┆ 0.842105   │
│ 1833 ┆ 26        ┆ 32        ┆ 38    ┆ 0.8125   ┆ 0.842105   │
│ 1834 ┆ 26        ┆ 38        ┆ 42    ┆ 0.684211 ┆ 0.904762   │
│ 1835 ┆ 30        ┆ 44        ┆ 51    ┆ 0.681818 ┆ 0.862745   │
│ 1836 ┆ 31        ┆ 47        ┆ 52    ┆ 0.659574 ┆ 0.903846   │
│ 1837 ┆ 22        ┆ 36        ┆ 41    ┆ 0.611111 ┆ 0.878049   │
│ 1838 ┆ 31        ┆ 36        ┆ 41    ┆ 0.861111 ┆ 0.878049   │
│ 1839 ┆ 24        ┆ 38        ┆ 43    ┆ 0.631579 ┆ 0.883721   │
│ 1840 ┆ 50        ┆ 66        ┆ 80    ┆ 0.757576 ┆ 0.825      │
│ 1841 ┆ 28        ┆ 46        ┆ 53    ┆ 0.608696 ┆ 0.867925   │
│ 1842 ┆ 38        ┆ 55        ┆ 70    ┆ 0.690909 ┆ 0.785714   │
│ 1843 ┆ 52        ┆ 70        ┆ 86    ┆ 0.742857 ┆ 0.813953   │
│ 1844 ┆ 64        ┆ 91        ┆ 106   ┆ 0.703297 ┆ 0.858491   │
│ 1845 ┆ 56        ┆ 75        ┆ 79    ┆ 0.746667 ┆ 0.949367   │
│ 1846 ┆ 57        ┆ 75        ┆ 90    ┆ 0.76     ┆ 0.833333   │
│ 1847 ┆ 60        ┆ 83        ┆ 97    ┆ 0.722892 ┆ 0.85567    │
│ 1848 ┆ 72        ┆ 90        ┆ 111   ┆ 0.8      ┆ 0.810811   │
│ 1849 ┆ 72        ┆ 97        ┆ 114   ┆ 0.742268 ┆ 0.850877   │
│ 1850 ┆ 76        ┆ 104       ┆ 116   ┆ 0.730769 ┆ 0.896552   │
│ …    ┆ …         ┆ …         ┆ …     ┆ …        ┆ …          │
│ 1975 ┆ 680       ┆ 1213      ┆ 4129  ┆ 0.560594 ┆ 0.293776   │
│ 1976 ┆ 739       ┆ 1233      ┆ 4195  ┆ 0.599351 ┆ 0.293921   │
│ 1977 ┆ 844       ┆ 1319      ┆ 4126  ┆ 0.639879 ┆ 0.31968    │
│ 1978 ┆ 1133      ┆ 1645      ┆ 4181  ┆ 0.688754 ┆ 0.393447   │
│ 1979 ┆ 1233      ┆ 1687      ┆ 4394  ┆ 0.730883 ┆ 0.383933   │
│ 1980 ┆ 1197      

In [177]:
podil_vazeb(df.filter(pl.col("stran") > 50))

shape: (224, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 1801 ┆ 3         ┆ 11        ┆ 12    ┆ 0.272727 ┆ 0.916667   │
│ 1802 ┆ 1         ┆ 10        ┆ 12    ┆ 0.1      ┆ 0.833333   │
│ 1803 ┆ 2         ┆ 11        ┆ 16    ┆ 0.181818 ┆ 0.6875     │
│ 1804 ┆ 6         ┆ 12        ┆ 17    ┆ 0.5      ┆ 0.705882   │
│ 1805 ┆ 6         ┆ 14        ┆ 16    ┆ 0.428571 ┆ 0.875      │
│ 1806 ┆ 4         ┆ 7         ┆ 9     ┆ 0.571429 ┆ 0.777778   │
│ 1807 ┆ 5         ┆ 13        ┆ 18    ┆ 0.384615 ┆ 0.722222   │
│ 1808 ┆ 5         ┆ 9         ┆ 14    ┆ 0.555556 ┆ 0.642857   │
│ 1809 ┆ 2         ┆ 12        ┆ 15    ┆ 0.166667 ┆ 0.8        │
│ 1810 ┆ 7         ┆ 12        ┆ 17    ┆ 0.583333 ┆ 0.705882   │
│ 1811 ┆ 5         ┆ 7         ┆ 10    ┆ 0.714286 ┆ 0.7        │
│ 1812 ┆ 12        ┆ 19        ┆ 21    ┆ 0.631579 ┆ 0.904762   │
│ 1813 ┆ 7         ┆ 14        ┆ 16    ┆ 0.5      ┆ 0.875      │
│ 1814 ┆ 8         ┆ 18        ┆ 23    ┆ 0.444444 ┆ 0.782609   │
│ 1815 ┆ 10        ┆ 18        ┆ 21    ┆ 0.555556 ┆ 0.857143   │
│ 1816 ┆ 8         ┆ 17        ┆ 22    ┆ 0.470588 ┆ 0.772727   │
│ 1817 ┆ 6         ┆ 18        ┆ 21    ┆ 0.333333 ┆ 0.857143   │
│ 1818 ┆ 17        ┆ 36        ┆ 39    ┆ 0.472222 ┆ 0.923077   │
│ 1819 ┆ 15        ┆ 35        ┆ 41    ┆ 0.428571 ┆ 0.853659   │
│ 1820 ┆ 12        ┆ 36        ┆ 41    ┆ 0.333333 ┆ 0.878049   │
│ 1821 ┆ 27        ┆ 46        ┆ 54    ┆ 0.586957 ┆ 0.851852   │
│ 1822 ┆ 23        ┆ 34        ┆ 42    ┆ 0.676471 ┆ 0.809524   │
│ 1823 ┆ 26        ┆ 40        ┆ 46    ┆ 0.65     ┆ 0.869565   │
│ 1824 ┆ 27        ┆ 42        ┆ 51    ┆ 0.642857 ┆ 0.823529   │
│ 1825 ┆ 27        ┆ 48        ┆ 55    ┆ 0.5625   ┆ 0.872727   │
│ 1826 ┆ 18        ┆ 32        ┆ 36    ┆ 0.5625   ┆ 0.888889   │
│ 1827 ┆ 23        ┆ 48        ┆ 55    ┆ 0.479167 ┆ 0.872727   │
│ 1828 ┆ 12        ┆ 41        ┆ 48    ┆ 0.292683 ┆ 0.854167   │
│ 1829 ┆ 16        ┆ 32        ┆ 36    ┆ 0.5      ┆ 0.888889   │
│ 1830 ┆ 27        ┆ 44        ┆ 56    ┆ 0.613636 ┆ 0.785714   │
│ 1831 ┆ 22        ┆ 42        ┆ 49    ┆ 0.52381  ┆ 0.857143   │
│ 1832 ┆ 15        ┆ 32        ┆ 38    ┆ 0.46875  ┆ 0.842105   │
│ 1833 ┆ 19        ┆ 32        ┆ 38    ┆ 0.59375  ┆ 0.842105   │
│ 1834 ┆ 23        ┆ 38        ┆ 42    ┆ 0.605263 ┆ 0.904762   │
│ 1835 ┆ 21        ┆ 44        ┆ 51    ┆ 0.477273 ┆ 0.862745   │
│ 1836 ┆ 16        ┆ 47        ┆ 52    ┆ 0.340426 ┆ 0.903846   │
│ 1837 ┆ 13        ┆ 36        ┆ 41    ┆ 0.361111 ┆ 0.878049   │
│ 1838 ┆ 24        ┆ 36        ┆ 41    ┆ 0.666667 ┆ 0.878049   │
│ 1839 ┆ 19        ┆ 38        ┆ 43    ┆ 0.5      ┆ 0.883721   │
│ 1840 ┆ 37        ┆ 66        ┆ 80    ┆ 0.560606 ┆ 0.825      │
│ 1841 ┆ 22        ┆ 46        ┆ 53    ┆ 0.478261 ┆ 0.867925   │
│ 1842 ┆ 25        ┆ 55        ┆ 70    ┆ 0.454545 ┆ 0.785714   │
│ 1843 ┆ 39        ┆ 70        ┆ 86    ┆ 0.557143 ┆ 0.813953   │
│ 1844 ┆ 48        ┆ 91        ┆ 106   ┆ 0.527473 ┆ 0.858491   │
│ 1845 ┆ 38        ┆ 75        ┆ 79    ┆ 0.506667 ┆ 0.949367   │
│ 1846 ┆ 38        ┆ 75        ┆ 90    ┆ 0.506667 ┆ 0.833333   │
│ 1847 ┆ 46        ┆ 83        ┆ 97    ┆ 0.554217 ┆ 0.85567    │
│ 1848 ┆ 42        ┆ 90        ┆ 111   ┆ 0.466667 ┆ 0.810811   │
│ 1849 ┆ 62        ┆ 97        ┆ 114   ┆ 0.639175 ┆ 0.850877   │
│ 1850 ┆ 53        ┆ 104       ┆ 116   ┆ 0.509615 ┆ 0.896552   │
│ …    ┆ …         ┆ …         ┆ …     ┆ …        ┆ …          │
│ 1975 ┆ 547       ┆ 1213      ┆ 4129  ┆ 0.450948 ┆ 0.293776   │
│ 1976 ┆ 600       ┆ 1233      ┆ 4195  ┆ 0.486618 ┆ 0.293921   │
│ 1977 ┆ 693       ┆ 1319      ┆ 4126  ┆ 0.525398 ┆ 0.31968    │
│ 1978 ┆ 960       ┆ 1645      ┆ 4181  ┆ 0.583587 ┆ 0.393447   │
│ 1979 ┆ 1046      ┆ 1687      ┆ 4394  ┆ 0.620036 ┆ 0.383933   │
│ 1980 ┆ 1011      

In [178]:
df.explode("655_a").group_by("655_a").len().sort(by="len",descending=True).head(100)

shape: (100, 2)
┌────────────────────────────────┬────────┐
│ 655_a                          ┆ len    │
│ ---                            ┆ ---    │
│ str                            ┆ u32    │
╞════════════════════════════════╪════════╡
│ null                           ┆ 219885 │
│ příručky                       ┆ 51782  │
│ učebnice vysokých škol         ┆ 42994  │
│ publikace pro děti             ┆ 36285  │
│ handbooks and manuals          ┆ 30675  │
│ children's literature          ┆ 28022  │
│ studie                         ┆ 23275  │
│ monografie                     ┆ 23142  │
│ textbooks (higher)             ┆ 19977  │
│ monographs                     ┆ 18527  │
│ populárně-naučné publikace     ┆ 17404  │
│ česká poezie                   ┆ 17181  │
│ české romány                   ┆ 16354  │
│ americké romány                ┆ 15734  │
│ American fiction               ┆ 14986  │
│ popular works                  ┆ 14372  │
│ Czech fiction                  ┆ 12582  │
│ Czech poetry                   ┆ 12418  │
│ publikace pro mládež           ┆ 9879   │
│ studies                        ┆ 9859   │
│ české příběhy                  ┆ 9392   │
│ učebnice středních škol        ┆ 9153   │
│ fotografické publikace         ┆ 9010   │
│ informační publikace           ┆ 8826   │
│ anglické romány                ┆ 8779   │
│ přehledy                       ┆ 8713   │
│ essays                         ┆ 8653   │
│ české povídky                  ┆ 8523   │
│ Czech stories                  ┆ 8454   │
│ biografie                      ┆ 8438   │
│ obrazové publikace             ┆ 8427   │
│ detektivní romány              ┆ 8297   │
│ pojednání                      ┆ 8287   │
│ English fiction                ┆ 8259   │
│ metodické příručky             ┆ 7905   │
│ photographical works           ┆ 7663   │
│ detective novels               ┆ 6712   │
│ pictorial works                ┆ 6678   │
│ učebnice základních škol       ┆ 6669   │
│ kolektivní monografie          ┆ 6560   │
│ collective monographs          ┆ 6470   │
│ sborníky                       ┆ 6153   │
│ autobiografické vzpomínky      ┆ 6086   │
│ information publications       ┆ 6033   │
│ kuchařské recepty              ┆ 5906   │
│ pracovní sešity                ┆ 5900   │
│ juvenile literature            ┆ 5827   │
│ historické romány              ┆ 5744   │
│ surveys                        ┆ 5655   │
│ české prózy                    ┆ 5642   │
│ fantasy romány                 ┆ 5573   │
│ fantasy novels                 ┆ 5488   │
│ biography                      ┆ 5448   │
│ příběhy                        ┆ 5344   │
│ milostné romány                ┆ 5290   │
│ autobiographical reminiscences ┆ 5275   │
│ úvahy                          ┆ 5265   │
│ activity books                 ┆ 5146   │
│ milostné povídky               ┆ 5081   │
│ cookbooks                      ┆ 4860   │
│ leporela                       ┆ 4798   │
│ CD-ROM                         ┆ 4738   │
│ učebnice                       ┆ 4679   │
│ methodological manuals         ┆ 4660   │
│ literatura faktu               ┆ 4640   │
│ dobrodružné povídky            ┆ 4638   │
│ brožury                        ┆ 4416   │
│ historical novels              ┆ 4199   │
│ katalogy výstav                ┆ 4172   │
│ folding picture-books          ┆ 4124   │
│ Czech short stories            ┆ 4098   │
│ romány                         ┆ 3974   │
│ Czech prose                    ┆ 3951   │
│ česká dramata                  ┆ 3926   │
│ výbory                         ┆ 3843   │
│ thrillery (romány)             ┆ 3836   │
│ thrillers (novels)             ┆ 3830   │
│ učební texty                   ┆ 3820   │
│ non-fiction                    ┆ 3792   │
│ dobrodružné romány             ┆ 3776   │
│ jubilejní publikace            ┆ 3695   │
│ průvodce                       ┆ 3666   │
│ vzpomínky                      ┆ 3642   │
│ textbooks (elementary)         ┆ 3528   │
│ stories                        ┆ 3517   │
│ vědecko-fantastické ro

In [179]:
podil_vazeb(df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "milostné povídky"))

shape: (37, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 1830 ┆ 1         ┆ 44        ┆ 56    ┆ 0.022727 ┆ 0.785714   │
│ 1923 ┆ 1         ┆ 1354      ┆ 3558  ┆ 0.000739 ┆ 0.380551   │
│ 1981 ┆ 1         ┆ 1399      ┆ 4298  ┆ 0.000715 ┆ 0.3255     │
│ 1990 ┆ 1         ┆ 4872      ┆ 5220  ┆ 0.000205 ┆ 0.933333   │
│ 1992 ┆ 9         ┆ 5843      ┆ 6371  ┆ 0.00154  ┆ 0.917124   │
│ 1993 ┆ 187       ┆ 6469      ┆ 7164  ┆ 0.028907 ┆ 0.902987   │
│ 1994 ┆ 526       ┆ 6613      ┆ 7436  ┆ 0.07954  ┆ 0.889322   │
│ 1995 ┆ 501       ┆ 7074      ┆ 8128  ┆ 0.070823 ┆ 0.870325   │
│ 1996 ┆ 300       ┆ 6847      ┆ 8513  ┆ 0.043815 ┆ 0.804299   │
│ 1997 ┆ 252       ┆ 7187      ┆ 9014  ┆ 0.035063 ┆ 0.797315   │
│ 1998 ┆ 226       ┆ 7169      ┆ 9103  ┆ 0.031525 ┆ 0.787543   │
│ 1999 ┆ 281       ┆ 7853      ┆ 9500  ┆ 0.035783 ┆ 0.826632   │
│ 2000 ┆ 180       ┆ 8282      ┆ 10141 ┆ 0.021734 ┆ 0.816685   │
│ 2001 ┆ 153       ┆ 8325      ┆ 10095 ┆ 0.018378 ┆ 0.824666   │
│ 2002 ┆ 74        ┆ 8417      ┆ 10210 ┆ 0.008792 ┆ 0.824388   │
│ 2003 ┆ 79        ┆ 8916      ┆ 10595 ┆ 0.00886  ┆ 0.841529   │
│ 2004 ┆ 92        ┆ 9244      ┆ 10953 ┆ 0.009952 ┆ 0.84397    │
│ 2005 ┆ 92        ┆ 9781      ┆ 11303 ┆ 0.009406 ┆ 0.865345   │
│ 2006 ┆ 61        ┆ 10294     ┆ 11924 ┆ 0.005926 ┆ 0.863301   │
│ 2007 ┆ 49        ┆ 10712     ┆ 12648 ┆ 0.004574 ┆ 0.846932   │
│ 2008 ┆ 86        ┆ 11286     ┆ 13183 ┆ 0.00762  ┆ 0.856103   │
│ 2009 ┆ 85        ┆ 10708     ┆ 12382 ┆ 0.007938 ┆ 0.864804   │
│ 2010 ┆ 75        ┆ 10989     ┆ 12779 ┆ 0.006825 ┆ 0.859926   │
│ 2011 ┆ 64        ┆ 11000     ┆ 12661 ┆ 0.005818 ┆ 0.86881    │
│ 2012 ┆ 21        ┆ 10860     ┆ 12690 ┆ 0.001934 ┆ 0.855792   │
│ 2013 ┆ 8         ┆ 10876     ┆ 12531 ┆ 0.000736 ┆ 0.867928   │
│ 2014 ┆ 6         ┆ 10829     ┆ 12656 ┆ 0.000554 ┆ 0.855642   │
│ 2015 ┆ 4         ┆ 11009     ┆ 12895 ┆ 0.000363 ┆ 0.853742   │
│ 2016 ┆ 5         ┆ 10667     ┆ 12347 ┆ 0.000469 ┆ 0.863935   │
│ 2017 ┆ 6         ┆ 10589     ┆ 12201 ┆ 0.000567 ┆ 0.86788    │
│ 2018 ┆ 4         ┆ 11020     ┆ 12566 ┆ 0.000363 ┆ 0.87697    │
│ 2019 ┆ 10        ┆ 10861     ┆ 12255 ┆ 0.000921 ┆ 0.886251   │
│ 2020 ┆ 2         ┆ 9997      ┆ 11279 ┆ 0.0002   ┆ 0.886337   │
│ 2021 ┆ 13        ┆ 10528     ┆ 11747 ┆ 0.001235 ┆ 0.896229   │
│ 2022 ┆ 5         ┆ 10878     ┆ 12059 ┆ 0.00046  ┆ 0.902065   │
│ 2023 ┆ 4         ┆ 9745      ┆ 10716 ┆ 0.00041  ┆ 0.909388   │
│ 2024 ┆ 6         ┆ 8842      ┆ 9540  ┆ 0.000679 ┆ 0.926834   │
└──────┴───────────┴───────────┴───────┴──────────┴────────────┘

In [180]:
podil_vazeb(df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "pracovní sešity"))

shape: (43, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 1937 ┆ 1         ┆ 1494      ┆ 4732  ┆ 0.000669 ┆ 0.315723   │
│ 1938 ┆ 2         ┆ 1270      ┆ 4018  ┆ 0.001575 ┆ 0.316078   │
│ 1975 ┆ 1         ┆ 1213      ┆ 4129  ┆ 0.000824 ┆ 0.293776   │
│ 1979 ┆ 1         ┆ 1687      ┆ 4394  ┆ 0.000593 ┆ 0.383933   │
│ 1983 ┆ 1         ┆ 3994      ┆ 4341  ┆ 0.00025  ┆ 0.920065   │
│ 1986 ┆ 3         ┆ 4584      ┆ 4680  ┆ 0.000654 ┆ 0.979487   │
│ 1988 ┆ 1         ┆ 4684      ┆ 4850  ┆ 0.000213 ┆ 0.965773   │
│ 1989 ┆ 3         ┆ 4677      ┆ 4969  ┆ 0.000641 ┆ 0.941236   │
│ 1990 ┆ 2         ┆ 4872      ┆ 5220  ┆ 0.000411 ┆ 0.933333   │
│ 1991 ┆ 5         ┆ 5288      ┆ 5705  ┆ 0.000946 ┆ 0.926906   │
│ 1992 ┆ 17        ┆ 5843      ┆ 6371  ┆ 0.002909 ┆ 0.917124   │
│ 1993 ┆ 27        ┆ 6469      ┆ 7164  ┆ 0.004174 ┆ 0.902987   │
│ 1994 ┆ 32        ┆ 6613      ┆ 7436  ┆ 0.004839 ┆ 0.889322   │
│ 1995 ┆ 36        ┆ 7074      ┆ 8128  ┆ 0.005089 ┆ 0.870325   │
│ 1996 ┆ 24        ┆ 6847      ┆ 8513  ┆ 0.003505 ┆ 0.804299   │
│ 1997 ┆ 37        ┆ 7187      ┆ 9014  ┆ 0.005148 ┆ 0.797315   │
│ 1998 ┆ 33        ┆ 7169      ┆ 9103  ┆ 0.004603 ┆ 0.787543   │
│ 1999 ┆ 40        ┆ 7853      ┆ 9500  ┆ 0.005094 ┆ 0.826632   │
│ 2000 ┆ 30        ┆ 8282      ┆ 10141 ┆ 0.003622 ┆ 0.816685   │
│ 2001 ┆ 25        ┆ 8325      ┆ 10095 ┆ 0.003003 ┆ 0.824666   │
│ 2002 ┆ 31        ┆ 8417      ┆ 10210 ┆ 0.003683 ┆ 0.824388   │
│ 2003 ┆ 44        ┆ 8916      ┆ 10595 ┆ 0.004935 ┆ 0.841529   │
│ 2004 ┆ 53        ┆ 9244      ┆ 10953 ┆ 0.005733 ┆ 0.84397    │
│ 2005 ┆ 40        ┆ 9781      ┆ 11303 ┆ 0.00409  ┆ 0.865345   │
│ 2006 ┆ 61        ┆ 10294     ┆ 11924 ┆ 0.005926 ┆ 0.863301   │
│ 2007 ┆ 66        ┆ 10712     ┆ 12648 ┆ 0.006161 ┆ 0.846932   │
│ 2008 ┆ 50        ┆ 11286     ┆ 13183 ┆ 0.00443  ┆ 0.856103   │
│ 2009 ┆ 73        ┆ 10708     ┆ 12382 ┆ 0.006817 ┆ 0.864804   │
│ 2010 ┆ 110       ┆ 10989     ┆ 12779 ┆ 0.01001  ┆ 0.859926   │
│ 2011 ┆ 80        ┆ 11000     ┆ 12661 ┆ 0.007273 ┆ 0.86881    │
│ 2012 ┆ 121       ┆ 10860     ┆ 12690 ┆ 0.011142 ┆ 0.855792   │
│ 2013 ┆ 103       ┆ 10876     ┆ 12531 ┆ 0.00947  ┆ 0.867928   │
│ 2014 ┆ 114       ┆ 10829     ┆ 12656 ┆ 0.010527 ┆ 0.855642   │
│ 2015 ┆ 99        ┆ 11009     ┆ 12895 ┆ 0.008993 ┆ 0.853742   │
│ 2016 ┆ 128       ┆ 10667     ┆ 12347 ┆ 0.012    ┆ 0.863935   │
│ 2017 ┆ 135       ┆ 10589     ┆ 12201 ┆ 0.012749 ┆ 0.86788    │
│ 2018 ┆ 124       ┆ 11020     ┆ 12566 ┆ 0.011252 ┆ 0.87697    │
│ 2019 ┆ 111       ┆ 10861     ┆ 12255 ┆ 0.01022  ┆ 0.886251   │
│ 2020 ┆ 151       ┆ 9997      ┆ 11279 ┆ 0.015105 ┆ 0.886337   │
│ 2021 ┆ 154       ┆ 10528     ┆ 11747 ┆ 0.014628 ┆ 0.896229   │
│ 2022 ┆ 129       ┆ 10878     ┆ 12059 ┆ 0.011859 ┆ 0.902065   │
│ 2023 ┆ 145       ┆ 9745      ┆ 10716 ┆ 0.014879 ┆ 0.909388   │
│ 2024 ┆ 75        ┆ 8842      ┆ 9540  ┆ 0.008482 ┆ 0.926834   │
└──────┴───────────┴───────────┴───────┴──────────┴────────────┘

In [181]:
podil_vazeb(df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "česká poezie"))

shape: (199, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 1802 ┆ 2         ┆ 10        ┆ 12    ┆ 0.2      ┆ 0.833333   │
│ 1803 ┆ 1         ┆ 11        ┆ 16    ┆ 0.090909 ┆ 0.6875     │
│ 1804 ┆ 2         ┆ 12        ┆ 17    ┆ 0.166667 ┆ 0.705882   │
│ 1805 ┆ 1         ┆ 14        ┆ 16    ┆ 0.071429 ┆ 0.875      │
│ 1810 ┆ 1         ┆ 12        ┆ 17    ┆ 0.083333 ┆ 0.705882   │
│ 1813 ┆ 2         ┆ 14        ┆ 16    ┆ 0.142857 ┆ 0.875      │
│ 1814 ┆ 1         ┆ 18        ┆ 23    ┆ 0.055556 ┆ 0.782609   │
│ 1816 ┆ 2         ┆ 17        ┆ 22    ┆ 0.117647 ┆ 0.772727   │
│ 1817 ┆ 3         ┆ 18        ┆ 21    ┆ 0.166667 ┆ 0.857143   │
│ 1821 ┆ 1         ┆ 46        ┆ 54    ┆ 0.021739 ┆ 0.851852   │
│ 1822 ┆ 4         ┆ 34        ┆ 42    ┆ 0.117647 ┆ 0.809524   │
│ 1823 ┆ 2         ┆ 40        ┆ 46    ┆ 0.05     ┆ 0.869565   │
│ 1827 ┆ 1         ┆ 48        ┆ 55    ┆ 0.020833 ┆ 0.872727   │
│ 1828 ┆ 1         ┆ 41        ┆ 48    ┆ 0.02439  ┆ 0.854167   │
│ 1831 ┆ 1         ┆ 42        ┆ 49    ┆ 0.02381  ┆ 0.857143   │
│ 1833 ┆ 1         ┆ 32        ┆ 38    ┆ 0.03125  ┆ 0.842105   │
│ 1835 ┆ 1         ┆ 44        ┆ 51    ┆ 0.022727 ┆ 0.862745   │
│ 1836 ┆ 3         ┆ 47        ┆ 52    ┆ 0.06383  ┆ 0.903846   │
│ 1837 ┆ 1         ┆ 36        ┆ 41    ┆ 0.027778 ┆ 0.878049   │
│ 1840 ┆ 2         ┆ 66        ┆ 80    ┆ 0.030303 ┆ 0.825      │
│ 1841 ┆ 2         ┆ 46        ┆ 53    ┆ 0.043478 ┆ 0.867925   │
│ 1842 ┆ 2         ┆ 55        ┆ 70    ┆ 0.036364 ┆ 0.785714   │
│ 1843 ┆ 3         ┆ 70        ┆ 86    ┆ 0.042857 ┆ 0.813953   │
│ 1845 ┆ 6         ┆ 75        ┆ 79    ┆ 0.08     ┆ 0.949367   │
│ 1846 ┆ 4         ┆ 75        ┆ 90    ┆ 0.053333 ┆ 0.833333   │
│ 1847 ┆ 1         ┆ 83        ┆ 97    ┆ 0.012048 ┆ 0.85567    │
│ 1848 ┆ 2         ┆ 90        ┆ 111   ┆ 0.022222 ┆ 0.810811   │
│ 1850 ┆ 1         ┆ 104       ┆ 116   ┆ 0.009615 ┆ 0.896552   │
│ 1851 ┆ 4         ┆ 110       ┆ 123   ┆ 0.036364 ┆ 0.894309   │
│ 1852 ┆ 3         ┆ 136       ┆ 152   ┆ 0.022059 ┆ 0.894737   │
│ 1853 ┆ 3         ┆ 121       ┆ 142   ┆ 0.024793 ┆ 0.852113   │
│ 1854 ┆ 2         ┆ 119       ┆ 132   ┆ 0.016807 ┆ 0.901515   │
│ 1855 ┆ 2         ┆ 86        ┆ 96    ┆ 0.023256 ┆ 0.895833   │
│ 1856 ┆ 4         ┆ 90        ┆ 105   ┆ 0.044444 ┆ 0.857143   │
│ 1857 ┆ 4         ┆ 112       ┆ 137   ┆ 0.035714 ┆ 0.817518   │
│ 1858 ┆ 9         ┆ 157       ┆ 175   ┆ 0.057325 ┆ 0.897143   │
│ 1859 ┆ 4         ┆ 114       ┆ 137   ┆ 0.035088 ┆ 0.832117   │
│ 1860 ┆ 2         ┆ 131       ┆ 148   ┆ 0.015267 ┆ 0.885135   │
│ 1861 ┆ 2         ┆ 163       ┆ 184   ┆ 0.01227  ┆ 0.88587    │
│ 1862 ┆ 9         ┆ 213       ┆ 236   ┆ 0.042254 ┆ 0.902542   │
│ 1863 ┆ 3         ┆ 281       ┆ 322   ┆ 0.010676 ┆ 0.872671   │
│ 1864 ┆ 4         ┆ 230       ┆ 256   ┆ 0.017391 ┆ 0.8984375  │
│ 1867 ┆ 5         ┆ 192       ┆ 210   ┆ 0.026042 ┆ 0.914286   │
│ 1868 ┆ 5         ┆ 250       ┆ 278   ┆ 0.02     ┆ 0.899281   │
│ 1869 ┆ 5         ┆ 221       ┆ 239   ┆ 0.022624 ┆ 0.924686   │
│ 1870 ┆ 3         ┆ 270       ┆ 299   ┆ 0.011111 ┆ 0.90301    │
│ 1871 ┆ 3         ┆ 225       ┆ 256   ┆ 0.013333 ┆ 0.878906   │
│ 1872 ┆ 3         ┆ 332       ┆ 372   ┆ 0.009036 ┆ 0.892473   │
│ 1873 ┆ 5         ┆ 329       ┆ 370   ┆ 0.015198 ┆ 0.889189   │
│ 1874 ┆ 7         ┆ 422       ┆ 487   ┆ 0.016588 ┆ 0.86653    │
│ …    ┆ …         ┆ …         ┆ …     ┆ …        ┆ …          │
│ 1975 ┆ 4         ┆ 1213      ┆ 4129  ┆ 0.003298 ┆ 0.293776   │
│ 1976 ┆ 2         ┆ 1233      ┆ 4195  ┆ 0.001622 ┆ 0.293921   │
│ 1977 ┆ 4         ┆ 1319      ┆ 4126  ┆ 0.003033 ┆ 0.31968    │
│ 1978 ┆ 6         ┆ 1645      ┆ 4181  ┆ 0.003647 ┆ 0.393447   │
│ 1979 ┆ 6         ┆ 1687      ┆ 4394  ┆ 0.003557 ┆ 0.383933   │
│ 1980 ┆ 2         

In [182]:
romany_isbn = df_isbn.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "české romány").select(pl.col('isbn')).to_series().to_list()
len(romany_isbn)

8955

In [183]:
romanove_vazby = podil_vazeb(df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "české romány"))
romanove_vazby

shape: (156, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 1843 ┆ 1         ┆ 70        ┆ 86    ┆ 0.014286 ┆ 0.813953   │
│ 1853 ┆ 1         ┆ 121       ┆ 142   ┆ 0.008264 ┆ 0.852113   │
│ 1854 ┆ 1         ┆ 119       ┆ 132   ┆ 0.008403 ┆ 0.901515   │
│ 1855 ┆ 4         ┆ 86        ┆ 96    ┆ 0.046512 ┆ 0.895833   │
│ 1857 ┆ 1         ┆ 112       ┆ 137   ┆ 0.008929 ┆ 0.817518   │
│ 1858 ┆ 2         ┆ 157       ┆ 175   ┆ 0.012739 ┆ 0.897143   │
│ 1860 ┆ 2         ┆ 131       ┆ 148   ┆ 0.015267 ┆ 0.885135   │
│ 1861 ┆ 3         ┆ 163       ┆ 184   ┆ 0.018405 ┆ 0.88587    │
│ 1862 ┆ 1         ┆ 213       ┆ 236   ┆ 0.004695 ┆ 0.902542   │
│ 1863 ┆ 2         ┆ 281       ┆ 322   ┆ 0.007117 ┆ 0.872671   │
│ 1864 ┆ 2         ┆ 230       ┆ 256   ┆ 0.008696 ┆ 0.8984375  │
│ 1865 ┆ 1         ┆ 231       ┆ 265   ┆ 0.004329 ┆ 0.871698   │
│ 1867 ┆ 2         ┆ 192       ┆ 210   ┆ 0.010417 ┆ 0.914286   │
│ 1868 ┆ 2         ┆ 250       ┆ 278   ┆ 0.008    ┆ 0.899281   │
│ 1869 ┆ 3         ┆ 221       ┆ 239   ┆ 0.013575 ┆ 0.924686   │
│ 1870 ┆ 2         ┆ 270       ┆ 299   ┆ 0.007407 ┆ 0.90301    │
│ 1871 ┆ 1         ┆ 225       ┆ 256   ┆ 0.004444 ┆ 0.878906   │
│ 1872 ┆ 1         ┆ 332       ┆ 372   ┆ 0.003012 ┆ 0.892473   │
│ 1873 ┆ 7         ┆ 329       ┆ 370   ┆ 0.021277 ┆ 0.889189   │
│ 1874 ┆ 4         ┆ 422       ┆ 487   ┆ 0.009479 ┆ 0.86653    │
│ 1875 ┆ 2         ┆ 383       ┆ 430   ┆ 0.005222 ┆ 0.890698   │
│ 1876 ┆ 1         ┆ 327       ┆ 364   ┆ 0.003058 ┆ 0.898352   │
│ 1877 ┆ 3         ┆ 286       ┆ 325   ┆ 0.01049  ┆ 0.88       │
│ 1878 ┆ 1         ┆ 331       ┆ 362   ┆ 0.003021 ┆ 0.914365   │
│ 1879 ┆ 2         ┆ 318       ┆ 365   ┆ 0.006289 ┆ 0.871233   │
│ 1880 ┆ 1         ┆ 411       ┆ 482   ┆ 0.002433 ┆ 0.852697   │
│ 1881 ┆ 5         ┆ 474       ┆ 536   ┆ 0.010549 ┆ 0.884328   │
│ 1882 ┆ 3         ┆ 466       ┆ 516   ┆ 0.006438 ┆ 0.903101   │
│ 1883 ┆ 2         ┆ 471       ┆ 537   ┆ 0.004246 ┆ 0.877095   │
│ 1884 ┆ 4         ┆ 467       ┆ 524   ┆ 0.008565 ┆ 0.891221   │
│ 1885 ┆ 4         ┆ 498       ┆ 562   ┆ 0.008032 ┆ 0.886121   │
│ 1886 ┆ 3         ┆ 478       ┆ 550   ┆ 0.006276 ┆ 0.869091   │
│ 1887 ┆ 2         ┆ 487       ┆ 540   ┆ 0.004107 ┆ 0.901852   │
│ 1888 ┆ 3         ┆ 488       ┆ 569   ┆ 0.006148 ┆ 0.857645   │
│ 1889 ┆ 5         ┆ 511       ┆ 605   ┆ 0.009785 ┆ 0.844628   │
│ 1890 ┆ 4         ┆ 632       ┆ 738   ┆ 0.006329 ┆ 0.856369   │
│ 1891 ┆ 3         ┆ 585       ┆ 675   ┆ 0.005128 ┆ 0.866667   │
│ 1892 ┆ 3         ┆ 667       ┆ 779   ┆ 0.004498 ┆ 0.856226   │
│ 1893 ┆ 7         ┆ 690       ┆ 798   ┆ 0.010145 ┆ 0.864662   │
│ 1894 ┆ 5         ┆ 730       ┆ 844   ┆ 0.006849 ┆ 0.864929   │
│ 1895 ┆ 4         ┆ 767       ┆ 868   ┆ 0.005215 ┆ 0.883641   │
│ 1896 ┆ 3         ┆ 794       ┆ 926   ┆ 0.003778 ┆ 0.857451   │
│ 1897 ┆ 9         ┆ 880       ┆ 1030  ┆ 0.010227 ┆ 0.854369   │
│ 1898 ┆ 3         ┆ 948       ┆ 1097  ┆ 0.003165 ┆ 0.864175   │
│ 1899 ┆ 6         ┆ 855       ┆ 988   ┆ 0.007018 ┆ 0.865385   │
│ 1900 ┆ 7         ┆ 980       ┆ 1170  ┆ 0.007143 ┆ 0.837607   │
│ 1901 ┆ 4         ┆ 671       ┆ 1519  ┆ 0.005961 ┆ 0.441738   │
│ 1902 ┆ 4         ┆ 816       ┆ 1718  ┆ 0.004902 ┆ 0.474971   │
│ 1903 ┆ 8         ┆ 784       ┆ 1643  ┆ 0.010204 ┆ 0.477176   │
│ 1904 ┆ 2         ┆ 694       ┆ 1608  ┆ 0.002882 ┆ 0.431592   │
│ …    ┆ …         ┆ …         ┆ …     ┆ …        ┆ …          │
│ 1974 ┆ 2         ┆ 1193      ┆ 4024  ┆ 0.001676 ┆ 0.296471   │
│ 1975 ┆ 5         ┆ 1213      ┆ 4129  ┆ 0.004122 ┆ 0.293776   │
│ 1976 ┆ 1         ┆ 1233      ┆ 4195  ┆ 0.000811 ┆ 0.293921   │
│ 1977 ┆ 5         ┆ 1319      ┆ 4126  ┆ 0.003791 ┆ 0.31968    │
│ 1978 ┆ 3         ┆ 1645      ┆ 4181  ┆ 0.001824 ┆ 0.393447   │
│ 1979 ┆ 4         

In [184]:
alt.Chart(alt_friendly(romanove_vazby.filter(pl.col("rok").is_between(1990,2024)))).mark_line().encode(alt.X("rok:T"), alt.Y("podíl:Q"))

alt.Chart(...)

In [185]:
bestsellerove_romanove_vazby = podil_vazeb(
    df.sort(by="rok").unique(
        subset=["100_a","245_a"]
    ).explode("655_a").filter(
        pl.col("655_a") == "české romány"
).explode("020_a").drop_nulls(
    subset=['020_a']
).with_columns(
    pl.col("020_a").map_elements(
        lambda x: x.replace('-','')
    ).alias("isbn")
).filter(
    pl.col("isbn").is_in(isbn_bestselleru)
))
bestsellerove_romanove_vazby

shape: (20, 6)
┌──────┬───────────┬───────────┬───────┬──────────┬────────────┐
│ rok  ┆ brožovaná ┆ jakákoliv ┆ vše   ┆ podíl    ┆ vyplněnost │
│ ---  ┆ ---       ┆ ---       ┆ ---   ┆ ---      ┆ ---        │
│ i64  ┆ u32       ┆ u32       ┆ u32   ┆ f64      ┆ f64        │
╞══════╪═══════════╪═══════════╪═══════╪══════════╪════════════╡
│ 2002 ┆ 2         ┆ 8417      ┆ 10210 ┆ 0.000238 ┆ 0.824388   │
│ 2004 ┆ 1         ┆ 9244      ┆ 10953 ┆ 0.000108 ┆ 0.84397    │
│ 2005 ┆ 2         ┆ 9781      ┆ 11303 ┆ 0.000204 ┆ 0.865345   │
│ 2006 ┆ 3         ┆ 10294     ┆ 11924 ┆ 0.000291 ┆ 0.863301   │
│ 2008 ┆ 3         ┆ 11286     ┆ 13183 ┆ 0.000266 ┆ 0.856103   │
│ 2009 ┆ 3         ┆ 10708     ┆ 12382 ┆ 0.00028  ┆ 0.864804   │
│ 2010 ┆ 3         ┆ 10989     ┆ 12779 ┆ 0.000273 ┆ 0.859926   │
│ 2011 ┆ 1         ┆ 11000     ┆ 12661 ┆ 0.000091 ┆ 0.86881    │
│ 2012 ┆ 3         ┆ 10860     ┆ 12690 ┆ 0.000276 ┆ 0.855792   │
│ 2014 ┆ 5         ┆ 10829     ┆ 12656 ┆ 0.000462 ┆ 0.855642   │
│ 2015 ┆ 1         ┆ 11009     ┆ 12895 ┆ 0.000091 ┆ 0.853742   │
│ 2016 ┆ 3         ┆ 10667     ┆ 12347 ┆ 0.000281 ┆ 0.863935   │
│ 2017 ┆ 4         ┆ 10589     ┆ 12201 ┆ 0.000378 ┆ 0.86788    │
│ 2018 ┆ 4         ┆ 11020     ┆ 12566 ┆ 0.000363 ┆ 0.87697    │
│ 2019 ┆ 1         ┆ 10861     ┆ 12255 ┆ 0.000092 ┆ 0.886251   │
│ 2020 ┆ 1         ┆ 9997      ┆ 11279 ┆ 0.0001   ┆ 0.886337   │
│ 2021 ┆ 3         ┆ 10528     ┆ 11747 ┆ 0.000285 ┆ 0.896229   │
│ 2022 ┆ 1         ┆ 10878     ┆ 12059 ┆ 0.000092 ┆ 0.902065   │
│ 2023 ┆ 7         ┆ 9745      ┆ 10716 ┆ 0.000718 ┆ 0.909388   │
│ 2024 ┆ 2         ┆ 8842      ┆ 9540  ┆ 0.000226 ┆ 0.926834   │
└──────┴───────────┴───────────┴───────┴──────────┴────────────┘

In [186]:
alt.Chart(alt_friendly(bestsellerove_romanove_vazby.filter(pl.col("rok").is_between(1990,2024)))).mark_line().encode(alt.X("rok:T"), alt.Y("podíl:Q"))

alt.Chart(...)

In [187]:
bestsellery = pd.read_json(os.path.join("data","sckn_zebricky.json"))
bestsellery = pl.from_pandas(bestsellery)
bestsellery
isbn_bestselleru = set(bestsellery.select(pl.col("sckn_isbn")).to_series().to_list())
df_isbn = df.explode("020_a").drop_nulls(subset=['020_a']).with_columns(pl.col("020_a").map_elements(lambda x: x.replace('-','')).alias("isbn"))

In [188]:
df_isbn.filter(pl.col('isbn').is_in(isbn_bestselleru))

shape: (6_468, 75)
┌──────────┬──────────────────────────┬────────────────┬────────────────┬───┬──────┬───────┬───────────┬───────────────┐
│ 100_ind1 ┆ 100_a                    ┆ 100_7          ┆ 100_4          ┆ … ┆ rok  ┆ stran ┆ vazba     ┆ isbn          │
│ ---      ┆ ---                      ┆ ---            ┆ ---            ┆   ┆ ---  ┆ ---   ┆ ---       ┆ ---           │
│ str      ┆ str                      ┆ str            ┆ list[str]      ┆   ┆ i64  ┆ i64   ┆ str       ┆ str           │
╞══════════╪══════════════════════════╪════════════════╪════════════════╪═══╪══════╪═══════╪═══════════╪═══════════════╡
│ 1        ┆ Rees, Laurence,          ┆ xx0030651      ┆ ["aut"]        ┆ … ┆ 2009 ┆ 431   ┆ pevná     ┆ 9788024225500 │
│ 1        ┆ Niven, Jennifer,         ┆ xx0172884      ┆ ["aut"]        ┆ … ┆ 2017 ┆ 406   ┆ brožovaná ┆ 9788075492647 │
│ 1        ┆ Kallentoft, Mons,        ┆ xx0133897      ┆ ["aut"]        ┆ … ┆ 2011 ┆ 440   ┆ pevná     ┆ 9788072944163 │
│ 1        ┆ Gott, Karel,             ┆ jk01032549     ┆ ["aut"]        ┆ … ┆ 2021 ┆ 690   ┆ pevná     ┆ 9788090822108 │
│ 1        ┆ Mina, Denise,            ┆ xx0026332      ┆ ["aut"]        ┆ … ┆ 2013 ┆ 406   ┆ pevná     ┆ 9788087697023 │
│ 1        ┆ Chrastilová, Brigita,    ┆ xx0011624      ┆ ["aut"]        ┆ … ┆ 2003 ┆ 565   ┆ pevná     ┆ 8086395634    │
│ 1        ┆ Vaňková, Ludmila,        ┆ jk01141586     ┆ ["aut"]        ┆ … ┆ 2011 ┆ 412   ┆ pevná     ┆ 9788072443000 │
│ 1        ┆ Peck, M. Scott           ┆ jn19990006438  ┆ ["aut"]        ┆ … ┆ 2011 ┆ 62    ┆ pevná     ┆ 9788026200130 │
│ 1        ┆ Lindgren, Astrid,        ┆ jn19990005095  ┆ ["aut"]        ┆ … ┆ 2002 ┆ 215   ┆ pevná     ┆ 8000010119    │
│ 1        ┆ Riordan, Rick,           ┆ xx0103318      ┆ ["aut"]        ┆ … ┆ 2010 ┆ 304   ┆ pevná     ┆ 9788025309742 │
│ 1        ┆ Lada, Josef,             ┆ jk01071364     ┆ ["ill"]        ┆ … ┆ 2017 ┆ 53    ┆ pevná     ┆ 9788027100170 │
│ 1        ┆ Mašín, Ctirad,           ┆ jn20000728402  ┆ ["aut"]        ┆ … ┆ 2010 ┆ 311   ┆ pevná     ┆ 9788020018304 │
│ 1        ┆ Wiking, Meik,            ┆ xx0212933      ┆ ["aut"]        ┆ … ┆ 2017 ┆ 287   ┆ pevná     ┆ 9788075651112 │
│ 1        ┆ Kate, Lauren,            ┆ xx0140244      ┆ ["aut"]        ┆ … ┆ 2012 ┆ 303   ┆ pevná     ┆ 9788024232393 │
│ 1        ┆ Kundera, Milan,          ┆ jk01070894     ┆ ["aui", "aut"] ┆ … ┆ 2017 ┆ 259   ┆ pevná     ┆ 9788071083672 │
│ 1        ┆ Barták, Matěj,           ┆ mzk2004261164  ┆ ["aut"]        ┆ … ┆ 2019 ┆ 323   ┆ pevná     ┆ 9788074283635 │
│ 1        ┆ Kate, Lauren,            ┆ xx0140244      ┆ ["aut"]        ┆ … ┆ 2011 ┆ 326   ┆ pevná     ┆ 9788024231518 │
│ 1        ┆ Irving, John,            ┆ jn19990003909  ┆ ["aut"]        ┆ … ┆ 2006 ┆ 877   ┆ pevná     ┆ 8020712186    │
│ 1        ┆ Koliš, Jiří,             ┆ ola2002146898  ┆ ["pht"]        ┆ … ┆ 2014 ┆ 334   ┆ pevná     ┆ 9788020432872 │
│ 1        ┆ Houellebecq, Michel,     ┆ xx0023237      ┆ ["aut"]        ┆ … ┆ 2015 ┆ 242   ┆ pevná     ┆ 9788020716538 │
│ 1        ┆ Viewegh, Michal,         ┆ jn19990010021  ┆ ["aut"]        ┆ … ┆ 2022 ┆ 230   ┆ pevná     ┆ 9788024947372 │
│ 1        ┆ Matthews, Rupert,        ┆ mzk2006356008  ┆ ["aut"]        ┆ … ┆ 2004 ┆ 78    ┆ pevná     ┆ 8071819999    │
│ 1        ┆ King, Stephen,           ┆ jn19990004346  ┆ ["aut"]        ┆ … ┆ 2019 ┆ 333   ┆ pevná     ┆ 9788075930897 │
│ 1        ┆ Sochrová, Marie          ┆ ola2003204957  ┆ ["aut"]        ┆ … ┆ 2004 ┆ 119   ┆ brožovaná ┆ 8072009737    │
│ 1        ┆ Lukšů, David,            ┆ xx0064998      ┆ ["aut"]        ┆ … ┆ 2015 ┆ 291   ┆ null      ┆ 9788074252402 │
│ 0        ┆ jaz                      ┆ jo2013798109   ┆ ["aut", "ill"] ┆ … ┆ 2015 ┆ 63    ┆ brožovaná ┆ 9788024756592 │
│ 1        ┆ Grisham, John,           ┆ jn20000602526  ┆ ["aut"]        ┆ … ┆ 2022 ┆ 260   ┆ pevná     ┆ 9788024279541 │
│ 1        ┆ Albright, Madeleine      ┆ jn19981000066  ┆ ["aut"]        ┆ … ┆ 2003 ┆ 551   ┆ pevná     ┆ 8072

In [189]:
alt.Chart(alt_friendly(romanove_vazby.filter(pl.col("rok").is_between(1990,2024)))).mark_line().encode(alt.X("rok:T"), alt.Y("podíl:Q"))

alt.Chart(...)

## Rozsah

In [191]:
rozsah = df.filter(~pl.col("stran").is_null()).group_by("rok").len().sort(by="rok").rename({"len":"vyplněno"})
rozsah = rozsah.join(df.group_by("rok").len().sort(by="rok").rename({"len":"vše"}), left_on="rok", right_on="rok", how="left")
rozsah = rozsah.with_columns((pl.col("vyplněno") / pl.col("vše")).alias("vyplněnost"))
rozsah

shape: (225, 4)
┌──────┬──────────┬───────┬────────────┐
│ rok  ┆ vyplněno ┆ vše   ┆ vyplněnost │
│ ---  ┆ ---      ┆ ---   ┆ ---        │
│ i64  ┆ u32      ┆ u32   ┆ f64        │
╞══════╪══════════╪═══════╪════════════╡
│ 1800 ┆ 1        ┆ 1     ┆ 1.0        │
│ 1801 ┆ 12       ┆ 12    ┆ 1.0        │
│ 1802 ┆ 12       ┆ 12    ┆ 1.0        │
│ 1803 ┆ 16       ┆ 16    ┆ 1.0        │
│ 1804 ┆ 17       ┆ 17    ┆ 1.0        │
│ 1805 ┆ 16       ┆ 16    ┆ 1.0        │
│ 1806 ┆ 9        ┆ 9     ┆ 1.0        │
│ 1807 ┆ 18       ┆ 18    ┆ 1.0        │
│ 1808 ┆ 14       ┆ 14    ┆ 1.0        │
│ 1809 ┆ 15       ┆ 15    ┆ 1.0        │
│ 1810 ┆ 17       ┆ 17    ┆ 1.0        │
│ 1811 ┆ 10       ┆ 10    ┆ 1.0        │
│ 1812 ┆ 21       ┆ 21    ┆ 1.0        │
│ 1813 ┆ 16       ┆ 16    ┆ 1.0        │
│ 1814 ┆ 23       ┆ 23    ┆ 1.0        │
│ 1815 ┆ 21       ┆ 21    ┆ 1.0        │
│ 1816 ┆ 22       ┆ 22    ┆ 1.0        │
│ 1817 ┆ 21       ┆ 21    ┆ 1.0        │
│ 1818 ┆ 39       ┆ 39    ┆ 1.0        │
│ 1819 ┆ 41       ┆ 41    ┆ 1.0        │
│ 1820 ┆ 41       ┆ 41    ┆ 1.0        │
│ 1821 ┆ 54       ┆ 54    ┆ 1.0        │
│ 1822 ┆ 42       ┆ 42    ┆ 1.0        │
│ 1823 ┆ 46       ┆ 46    ┆ 1.0        │
│ 1824 ┆ 51       ┆ 51    ┆ 1.0        │
│ 1825 ┆ 55       ┆ 55    ┆ 1.0        │
│ 1826 ┆ 36       ┆ 36    ┆ 1.0        │
│ 1827 ┆ 55       ┆ 55    ┆ 1.0        │
│ 1828 ┆ 48       ┆ 48    ┆ 1.0        │
│ 1829 ┆ 36       ┆ 36    ┆ 1.0        │
│ 1830 ┆ 56       ┆ 56    ┆ 1.0        │
│ 1831 ┆ 49       ┆ 49    ┆ 1.0        │
│ 1832 ┆ 38       ┆ 38    ┆ 1.0        │
│ 1833 ┆ 38       ┆ 38    ┆ 1.0        │
│ 1834 ┆ 42       ┆ 42    ┆ 1.0        │
│ 1835 ┆ 51       ┆ 51    ┆ 1.0        │
│ 1836 ┆ 52       ┆ 52    ┆ 1.0        │
│ 1837 ┆ 41       ┆ 41    ┆ 1.0        │
│ 1838 ┆ 41       ┆ 41    ┆ 1.0        │
│ 1839 ┆ 43       ┆ 43    ┆ 1.0        │
│ 1840 ┆ 80       ┆ 80    ┆ 1.0        │
│ 1841 ┆ 53       ┆ 53    ┆ 1.0        │
│ 1842 ┆ 70       ┆ 70    ┆ 1.0        │
│ 1843 ┆ 86       ┆ 86    ┆ 1.0        │
│ 1844 ┆ 106      ┆ 106   ┆ 1.0        │
│ 1845 ┆ 79       ┆ 79    ┆ 1.0        │
│ 1846 ┆ 90       ┆ 90    ┆ 1.0        │
│ 1847 ┆ 97       ┆ 97    ┆ 1.0        │
│ 1848 ┆ 111      ┆ 111   ┆ 1.0        │
│ 1849 ┆ 114      ┆ 114   ┆ 1.0        │
│ …    ┆ …        ┆ …     ┆ …          │
│ 1975 ┆ 4129     ┆ 4129  ┆ 1.0        │
│ 1976 ┆ 4195     ┆ 4195  ┆ 1.0        │
│ 1977 ┆ 4126     ┆ 4126  ┆ 1.0        │
│ 1978 ┆ 4181     ┆ 4181  ┆ 1.0        │
│ 1979 ┆ 4394     ┆ 4394  ┆ 1.0        │
│ 1980 ┆ 4461     ┆ 4461  ┆ 1.0        │
│ 1981 ┆ 4297     ┆ 4298  ┆ 0.999767   │
│ 1982 ┆ 4388     ┆ 4388  ┆ 1.0        │
│ 1983 ┆ 4341     ┆ 4341  ┆ 1.0        │
│ 1984 ┆ 4589     ┆ 4589  ┆ 1.0        │
│ 1985 ┆ 4506     ┆ 4506  ┆ 1.0        │
│ 1986 ┆ 4680     ┆ 4680  ┆ 1.0        │
│ 1987 ┆ 4781     ┆ 4781  ┆ 1.0        │
│ 1988 ┆ 4850     ┆ 4850  ┆ 1.0        │
│ 1989 ┆ 4969     ┆ 4969  ┆ 1.0        │
│ 1990 ┆ 5220     ┆ 5220  ┆ 1.0        │
│ 1991 ┆ 5705     ┆ 5705  ┆ 1.0        │
│ 1992 ┆ 6371     ┆ 6371  ┆ 1.0        │
│ 1993 ┆ 7164     ┆ 7164  ┆ 1.0        │
│ 1994 ┆ 7436     ┆ 7436  ┆ 1.0        │
│ 1995 ┆ 8128     ┆ 8128  ┆ 1.0        │
│ 1996 ┆ 8513     ┆ 8513  ┆ 1.0        │
│ 1997 ┆ 9014     ┆ 9014  ┆ 1.0        │
│ 1998 ┆ 9102     ┆ 9103  ┆ 0.99989    │
│ 1999 ┆ 9500     ┆ 9500  ┆ 1.0        │
│ 2000 ┆ 10137    ┆ 10141 ┆ 0.999606   │
│ 2001 ┆ 10092    ┆ 10095 ┆ 0.999703   │
│ 2002 ┆ 10203    ┆ 10210 ┆ 0.999314   │
│ 2003 ┆ 10588    ┆ 10595 ┆ 0.999339   │
│ 2004 ┆ 10944    ┆ 10953 ┆ 0.999178   │
│ 2005 ┆ 11296    ┆ 11303 ┆ 0.999381   │
│ 2006 ┆ 11920    ┆ 11924 ┆ 0.999665   │
│ 2007 ┆ 12641    ┆ 12648 ┆ 0.999447   │
│ 2008 ┆ 13183    ┆ 13183 ┆ 1.0        │
│ 2009 ┆ 12380    ┆ 12382 ┆ 0.999838   │
│ 2010 ┆ 12779    ┆ 12779 ┆ 1.0        │
│ 2011 ┆ 12661    ┆ 12661 ┆ 1.0        │
│ 2012 ┆ 12690    ┆ 12690 ┆ 1.0        │
│ 2013 ┆ 12531    ┆ 12531 ┆ 1.0        │
│ 2014 ┆ 12656    ┆ 12656 ┆ 1.0        │
│ 2015 ┆ 12895    ┆ 12895 ┆ 1.0        │
│ 2016 

In [192]:
def streni_tloustka(frejm):
    return frejm.group_by("rok").agg(pl.col("stran").median()).sort(by="rok").with_columns(
                   pl.col("rok").map_elements(
                       lambda x: datetime.date(year=int(x), month=1, day=1), 
                       return_dtype=pl.Date
                   ).cast(pl.Datetime))

In [193]:
tloustky_romanu = df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "české romány").filter(pl.col("rok") >= 1990).with_columns(
                   pl.col("rok").map_elements(
                       lambda x: datetime.date(year=int(x), month=1, day=1), 
                       return_dtype=pl.Date
                   ).cast(pl.Datetime))

In [194]:
tloustky_romanu.select(pl.col("stran"))

shape: (8_531, 1)
┌───────┐
│ stran │
│ ---   │
│ i64   │
╞═══════╡
│ 223   │
│ 363   │
│ 444   │
│ 145   │
│ 247   │
│ 237   │
│ 179   │
│ 164   │
│ 125   │
│ 156   │
│ 278   │
│ 181   │
│ 188   │
│ 157   │
│ 125   │
│ 119   │
│ 224   │
│ 351   │
│ 350   │
│ 233   │
│ 322   │
│ 118   │
│ 248   │
│ 403   │
│ 189   │
│ 302   │
│ 278   │
│ 218   │
│ 276   │
│ 204   │
│ 255   │
│ 223   │
│ 307   │
│ 197   │
│ 162   │
│ 285   │
│ 186   │
│ 147   │
│ 113   │
│ 286   │
│ 156   │
│ 290   │
│ 278   │
│ 569   │
│ 293   │
│ 278   │
│ 205   │
│ 261   │
│ 279   │
│ 203   │
│ …     │
│ 460   │
│ 127   │
│ 226   │
│ 425   │
│ 238   │
│ 556   │
│ 227   │
│ 200   │
│ 166   │
│ 159   │
│ 273   │
│ 141   │
│ 335   │
│ 270   │
│ 381   │
│ 220   │
│ 247   │
│ 281   │
│ 213   │
│ 365   │
│ 240   │
│ 311   │
│ 340   │
│ 361   │
│ 201   │
│ 468   │
│ 222   │
│ 297   │
│ 229   │
│ 191   │
│ 238   │
│ 221   │
│ 396   │
│ 274   │
│ 494   │
│ 219   │
│ 270   │
│ 235   │
│ 242   │
│ 269   │
│ 287   │
│ 227   │
│ 181   │
│ 177   │
│ 183   │
│ 246   │
│ 168   │
│ 219   │
│ 445   │
│ 220   │
└───────┘

In [195]:
tloustky_romanu.sort(by='stran',descending=True).select(pl.col(["rok","100_a","245_a","stran"]))

shape: (8_531, 4)
┌─────────────────────┬─────────────────────────┬─────────────────────────────────┬───────┐
│ rok                 ┆ 100_a                   ┆ 245_a                           ┆ stran │
│ ---                 ┆ ---                     ┆ ---                             ┆ ---   │
│ datetime[μs]        ┆ str                     ┆ str                             ┆ i64   │
╞═════════════════════╪═════════════════════════╪═════════════════════════════════╪═══════╡
│ 2021-01-01 00:00:00 ┆ Motýl, Petr,            ┆ Šatna a klášter                 ┆ 1193  │
│ 2005-01-01 00:00:00 ┆ Slanská, Mariana        ┆ Tóny v trní                     ┆ 1101  │
│ 2014-01-01 00:00:00 ┆ Novotný, František,     ┆ Valhala                         ┆ 1086  │
│ 2024-01-01 00:00:00 ┆ BasthArt,               ┆ Bastard                         ┆ 1085  │
│ 2024-01-01 00:00:00 ┆ Beneš, Filip,           ┆ Černý měsíc                     ┆ 1000  │
│ 2019-01-01 00:00:00 ┆ Hyrsch, Áron,           ┆ Hora rabínova                   ┆ 929   │
│ 2023-01-01 00:00:00 ┆ Šalda, Ladislav,        ┆ Ta hra neměla pravidla          ┆ 868   │
│ 2020-01-01 00:00:00 ┆ Kučera, Dalibor,        ┆ Poté                            ┆ 836   │
│ 2018-01-01 00:00:00 ┆ Dobeš, Jára,            ┆ Stigmata karmy                  ┆ 816   │
│ 2017-01-01 00:00:00 ┆ Svobodová, Jitka        ┆ Přemyslova krev                 ┆ 812   │
│ 2021-01-01 00:00:00 ┆ Levithann, Revy,        ┆ Vrah z Bellevillu               ┆ 796   │
│ 2010-01-01 00:00:00 ┆ Fiala, Dominik,         ┆ Láska až za hrob                ┆ 786   │
│ 2019-01-01 00:00:00 ┆ Vondruška, Vlastimil,   ┆ Kronika zániku Evropy           ┆ 779   │
│ 2004-01-01 00:00:00 ┆ Novák, Jan,             ┆ Zatím dobrý                     ┆ 776   │
│ 2007-01-01 00:00:00 ┆ Filip, Ota,             ┆ Osmý, čili, Nedokončený životo… ┆ 773   │
│ 2022-01-01 00:00:00 ┆ Lipner, Tomáš,          ┆ Hvězdolet Vltava                ┆ 765   │
│ 2021-01-01 00:00:00 ┆ Horák, Ondřej,          ┆ Pohlavní styky                  ┆ 759   │
│ 2019-01-01 00:00:00 ┆ Štolba, Jan,            ┆ Nezastavitelný den              ┆ 756   │
│ 2021-01-01 00:00:00 ┆ Hamouz, Jan,            ┆ Třetí ucho                      ┆ 756   │
│ 1999-01-01 00:00:00 ┆ Skarlant, Petr,         ┆ Věk rozkoší                     ┆ 753   │
│ 2011-01-01 00:00:00 ┆ Kučera, Dalibor,        ┆ Dům soumraku                    ┆ 752   │
│ 2024-01-01 00:00:00 ┆ Krejčík, Přemysl,       ┆ Rochus                          ┆ 751   │
│ 2018-01-01 00:00:00 ┆ Denemarková, Radka,     ┆ Hodiny z olova                  ┆ 747   │
│ 2019-01-01 00:00:00 ┆ Bareš, Pavel,           ┆ Kronovy děti                    ┆ 746   │
│ 2016-01-01 00:00:00 ┆ Vaňková, Ludmila,       ┆ Karel IV.                       ┆ 743   │
│ 2017-01-01 00:00:00 ┆ Šlejhar, Josef Karel,   ┆ Cvrček mého krbu                ┆ 739   │
│ 2022-01-01 00:00:00 ┆ Velinský, Jaroslav,     ┆ Případy Augustina Velikého & s… ┆ 738   │
│ 2024-01-01 00:00:00 ┆ Haidingerová, Kristina, ┆ Očistec                         ┆ 734   │
│ 1992-01-01 00:00:00 ┆ Zima, Stanislav,        ┆ Pravda o zkáze Sodomy           ┆ 733   │
│ 2019-01-01 00:00:00 ┆ Ajvaz, Michal,          ┆ Města                           ┆ 724   │
│ 1999-01-01 00:00:00 ┆ Macura, Vladimír,       ┆ Ten, který bude                 ┆ 718   │
│ 2022-01-01 00:00:00 ┆ Cima, Anna,             ┆ Vzpomínky na úhoře              ┆ 718   │
│ 2014-01-01 00:00:00 ┆ Kahuda, Václav,         ┆ Vítr, tma, přítomnost           ┆ 715   │
│ 1996-01-01 00:00:00 ┆ Kohout, Pavel,          ┆ Konec velkých prázdnin          ┆ 711   │
│ 2023-01-01 00:00:00 ┆ Ruščáková, Dagmar       ┆ Alžběta a drak                  ┆ 710   │
│ 2023-01-01 00:00:00 ┆ Petrásek, Tomáš,        ┆ Azhareida                       ┆ 705   │
│ 2008-01-01 00:00:00 ┆ Mlynkec, Tomáš,         ┆ Slavíci kamenného mostu         ┆ 704   │
│ 2024-01-01 00:00:00 ┆ Škabraha, Martin,       ┆ Kníže Moravanů                  ┆ 692   │
│ 2014-01-01 00:00:00 ┆ Hl

In [196]:
do_grafu = tloustky_romanu.filter(pl.col("stran") >= 30).group_by("rok").agg(pl.col("stran").quantile(0.25).alias('malo')).join(
    tloustky_romanu.filter(pl.col("stran") >= 30).group_by("rok").agg(pl.col("stran").quantile(0.75).alias('hodne')), on="rok"
).join(
    tloustky_romanu.filter(pl.col("stran") >= 30).group_by("rok").agg(pl.col("stran").median().alias('median')), on="rok"
).join(
    tloustky_romanu.filter(pl.col("stran") >= 30).group_by("rok").agg(pl.col("stran").min().alias('min')), on="rok"
).join(
    tloustky_romanu.filter(pl.col("stran") >= 30).group_by("rok").agg(pl.col("stran").max().alias('max')), on="rok"
).to_pandas()
do_grafu

rok   malo  hodne  median  min   max
0  1991-01-01  120.0  253.0   191.0   40   486
1  2023-01-01  218.0  344.0   272.0   49   868
2  2020-01-01  212.0  321.0   259.5   99   836
3  2010-01-01  188.0  285.0   223.0   91   786
4  2017-01-01  206.0  319.0   254.0   96   812
5  2004-01-01  150.0  285.0   214.0   82   776
6  2018-01-01  214.0  320.0   253.0   44   816
7  2005-01-01  160.0  274.0   215.0   61  1101
8  2009-01-01  159.0  286.0   223.0   52   634
9  2019-01-01  209.0  335.0   260.0   94   929
10 2022-01-01  213.0  336.0   271.0   91   765
11 2011-01-01  177.0  293.0   224.0   84   752
12 2015-01-01  210.0  322.0   257.0   82   623
13 2013-01-01  195.0  283.0   236.0   79   636
14 1990-01-01  204.0  326.0   254.0   70   583
15 2014-01-01  209.0  311.0   248.5   64  1086
16 2003-01-01  141.0  279.0   204.0   91   685
17 1995-01-01  147.0  223.0   181.0   63   502
18 2001-01-01  137.0  253.0   181.0   92   684
19 2021-01-01  212.0  335.0   267.0   62  1193
20 1992-01-01  124.0  222.0   158.0   48   733
21 1997-01-01  142.0  245.0   220.5  101   380
22 2024-01-01  221.0  349.0   281.0   82  1085
23 1998-01-01  158.0  237.0   195.0   98   407
24 1996-01-01  176.0  255.0   222.0  101   711
25 2008-01-01  159.0  287.0   222.0   83   704
26 2006-01-01  158.0  289.0   222.0  102   579
27 2012-01-01  184.0  309.0   234.5   58   645
28 2007-01-01  171.0  295.0   222.0   99   773
29 1999-01-01  143.0  269.0   191.0  105   753
30 1994-01-01  158.0  270.0   193.0  117   429
31 2000-01-01  142.0  251.0   189.0   94   622
32 2002-01-01  145.0  258.0   199.0   85   637
33 1993-01-01  111.0  224.0   176.0   57   606
34 2016-01-01  207.0  319.0   256.5   39   743

In [197]:
streni_tloustka(df.sort(by="rok").unique(subset=["100_a","245_a"]).explode("655_a").filter(pl.col("655_a") == "české romány"))

shape: (174, 2)
┌─────────────────────┬───────┐
│ rok                 ┆ stran │
│ ---                 ┆ ---   │
│ datetime[μs]        ┆ f64   │
╞═════════════════════╪═══════╡
│ 1814-01-01 00:00:00 ┆ 71.0  │
│ 1818-01-01 00:00:00 ┆ 196.0 │
│ 1843-01-01 00:00:00 ┆ 152.0 │
│ 1848-01-01 00:00:00 ┆ 161.0 │
│ 1853-01-01 00:00:00 ┆ 173.0 │
│ 1854-01-01 00:00:00 ┆ 303.0 │
│ 1855-01-01 00:00:00 ┆ 223.5 │
│ 1857-01-01 00:00:00 ┆ 207.0 │
│ 1858-01-01 00:00:00 ┆ 200.0 │
│ 1860-01-01 00:00:00 ┆ 249.0 │
│ 1861-01-01 00:00:00 ┆ 212.0 │
│ 1862-01-01 00:00:00 ┆ 372.5 │
│ 1863-01-01 00:00:00 ┆ 385.0 │
│ 1864-01-01 00:00:00 ┆ 193.5 │
│ 1865-01-01 00:00:00 ┆ 380.0 │
│ 1866-01-01 00:00:00 ┆ 395.0 │
│ 1867-01-01 00:00:00 ┆ 319.0 │
│ 1868-01-01 00:00:00 ┆ 336.0 │
│ 1869-01-01 00:00:00 ┆ 228.0 │
│ 1870-01-01 00:00:00 ┆ 416.0 │
│ 1871-01-01 00:00:00 ┆ 290.0 │
│ 1872-01-01 00:00:00 ┆ 545.5 │
│ 1873-01-01 00:00:00 ┆ 223.0 │
│ 1874-01-01 00:00:00 ┆ 353.0 │
│ 1875-01-01 00:00:00 ┆ 212.0 │
│ 1876-01-01 00:00:00 ┆ 318.0 │
│ 1877-01-01 00:00:00 ┆ 118.0 │
│ 1878-01-01 00:00:00 ┆ 317.0 │
│ 1879-01-01 00:00:00 ┆ 277.0 │
│ 1880-01-01 00:00:00 ┆ 263.0 │
│ 1881-01-01 00:00:00 ┆ 376.0 │
│ 1882-01-01 00:00:00 ┆ 224.0 │
│ 1883-01-01 00:00:00 ┆ 312.0 │
│ 1884-01-01 00:00:00 ┆ 285.0 │
│ 1885-01-01 00:00:00 ┆ 295.0 │
│ 1886-01-01 00:00:00 ┆ 241.0 │
│ 1887-01-01 00:00:00 ┆ 308.0 │
│ 1888-01-01 00:00:00 ┆ 268.0 │
│ 1889-01-01 00:00:00 ┆ 200.0 │
│ 1890-01-01 00:00:00 ┆ 196.0 │
│ 1891-01-01 00:00:00 ┆ 173.0 │
│ 1892-01-01 00:00:00 ┆ 223.0 │
│ 1893-01-01 00:00:00 ┆ 227.0 │
│ 1894-01-01 00:00:00 ┆ 317.0 │
│ 1895-01-01 00:00:00 ┆ 229.0 │
│ 1896-01-01 00:00:00 ┆ 244.0 │
│ 1897-01-01 00:00:00 ┆ 278.0 │
│ 1898-01-01 00:00:00 ┆ 256.0 │
│ 1899-01-01 00:00:00 ┆ 297.5 │
│ 1900-01-01 00:00:00 ┆ 236.0 │
│ …                   ┆ …     │
│ 1975-01-01 00:00:00 ┆ 168.5 │
│ 1976-01-01 00:00:00 ┆ 241.5 │
│ 1977-01-01 00:00:00 ┆ 233.5 │
│ 1978-01-01 00:00:00 ┆ 186.5 │
│ 1979-01-01 00:00:00 ┆ 265.0 │
│ 1980-01-01 00:00:00 ┆ 179.5 │
│ 1981-01-01 00:00:00 ┆ 201.5 │
│ 1982-01-01 00:00:00 ┆ 221.0 │
│ 1983-01-01 00:00:00 ┆ 259.0 │
│ 1984-01-01 00:00:00 ┆ 213.5 │
│ 1985-01-01 00:00:00 ┆ 258.5 │
│ 1986-01-01 00:00:00 ┆ 190.0 │
│ 1987-01-01 00:00:00 ┆ 223.5 │
│ 1988-01-01 00:00:00 ┆ 221.0 │
│ 1989-01-01 00:00:00 ┆ 231.5 │
│ 1990-01-01 00:00:00 ┆ 254.0 │
│ 1991-01-01 00:00:00 ┆ 191.0 │
│ 1992-01-01 00:00:00 ┆ 158.0 │
│ 1993-01-01 00:00:00 ┆ 176.0 │
│ 1994-01-01 00:00:00 ┆ 193.0 │
│ 1995-01-01 00:00:00 ┆ 181.0 │
│ 1996-01-01 00:00:00 ┆ 222.0 │
│ 1997-01-01 00:00:00 ┆ 220.5 │
│ 1998-01-01 00:00:00 ┆ 195.0 │
│ 1999-01-01 00:00:00 ┆ 191.0 │
│ 2000-01-01 00:00:00 ┆ 189.0 │
│ 2001-01-01 00:00:00 ┆ 181.0 │
│ 2002-01-01 00:00:00 ┆ 199.0 │
│ 2003-01-01 00:00:00 ┆ 203.0 │
│ 2004-01-01 00:00:00 ┆ 213.5 │
│ 2005-01-01 00:00:00 ┆ 215.0 │
│ 2006-01-01 00:00:00 ┆ 222.0 │
│ 2007-01-01 00:00:00 ┆ 222.0 │
│ 2008-01-01 00:00:00 ┆ 222.0 │
│ 2009-01-01 00:00:00 ┆ 223.0 │
│ 2010-01-01 00:00:00 ┆ 223.0 │
│ 2011-01-01 00:00:00 ┆ 223.0 │
│ 2012-01-01 00:00:00 ┆ 234.0 │
│ 2013-01-01 00:00:00 ┆ 227.5 │
│ 2014-01-01 00:00:00 ┆ 247.0 │
│ 2015-01-01 00:00:00 ┆ 256.0 │
│ 2016-01-01 00:00:00 ┆ 254.0 │
│ 2017-01-01 00:00:00 ┆ 253.0 │
│ 2018-01-01 00:00:00 ┆ 253.0 │
│ 2019-01-01 00:00:00 ┆ 259.0 │
│ 2020-01-01 00:00:00 ┆ 259.0 │
│ 2021-01-01 00:00:00 ┆ 266.5 │
│ 2022-01-01 00:00:00 ┆ 270.0 │
│ 2023-01-01 00:00:00 ┆ 271.0 │
│ 2024-01-01 00:00:00 ┆ 281.0 │
└─────────────────────┴───────┘

In [198]:
rozptyl = alt.Chart(do_grafu, title=alt.Title("Jak bobtná český román", subtitle=["Do pásu se rozsahem vejde 50 % knih. Tečky jsou ty nejtlustší."]), width=300, height=400).mark_area(opacity=0.5).encode(
       alt.X("rok:T", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')).title(None),
    alt.Y("hodne:Q", axis=alt.Axis(domainOpacity=0, format='d', tickColor='#DCDDD6')).title(None),
    alt.Y2("malo:Q")
)

median = alt.Chart(do_grafu, width=300).mark_line().encode(
       alt.X("rok:T", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')),
    alt.Y("median:Q", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6'))
)

kraje = alt.Chart(do_grafu, width=300).mark_point(size=2).encode(
       alt.X("rok:T", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')),
    alt.Y("max:Q", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6'))
)


finale = (rozptyl + median + kraje).configure_view(stroke='transparent')

finale

alt.LayerChart(...)

In [199]:
gr = pd.read_csv(os.path.join('data','goodreads-hodnoceni.csv'))
gr = pl.from_pandas(gr)
gr = gr.sort(by="GR_date").unique(subset=['GR_isbn'],keep='last')
dk = pd.read_csv(os.path.join('data','databazeknih-hodnoceni.csv'))
dk = pl.from_pandas(dk)
dk = dk.sort(by="DK_date").unique(subset=['DK_isbn'],keep='last')

In [242]:
dk

shape: (2_576, 16)
┌───────────┬────────────┬────────────────┬───────────┬───┬────────────────┬────────────────┬───────────────┬──────────┐
│ DK_isbn   ┆ DK_date    ┆ DK_titul       ┆ DK_rating ┆ … ┆ DK_dalších_sez ┆ DK_Doporučenýc ┆ DK_autorstvo  ┆ DK_vyslo │
│ ---       ┆ ---        ┆ ---            ┆ ---       ┆   ┆ namech         ┆ h              ┆ ---           ┆ ---      │
│ f64       ┆ str        ┆ str            ┆ f64       ┆   ┆ ---            ┆ ---            ┆ str           ┆ f64      │
│           ┆            ┆                ┆           ┆   ┆ f64            ┆ f64            ┆               ┆          │
╞═══════════╪════════════╪════════════════╪═══════════╪═══╪════════════════╪════════════════╪═══════════════╪══════════╡
│ 9.7880e12 ┆ 2024-12-09 ┆ Můj rok 1963   ┆ 60.0      ┆ … ┆ null           ┆ null           ┆ ['Alena       ┆ 2023.0   │
│           ┆ 03:44:30   ┆                ┆           ┆   ┆                ┆                ┆ Breuerová']   ┆          │
│ 9.7880e12 ┆ 2024-12-09 ┆ Likvidátor     ┆ 84.0      ┆ … ┆ 3.0            ┆ 5.0            ┆ ['Honza       ┆ 2023.0   │
│           ┆ 03:42:29   ┆                ┆           ┆   ┆                ┆                ┆ Slívka']      ┆          │
│ 9.7881e12 ┆ 2024-12-09 ┆ Luftwaffe 1935 ┆ 55.0      ┆ … ┆ 2.0            ┆ null           ┆ ['Marek       ┆ 2022.0   │
│           ┆ 03:36:12   ┆                ┆           ┆   ┆                ┆                ┆ Brzkovský']   ┆          │
│ 9.7881e12 ┆ 2024-12-09 ┆ Závistivá      ┆ 100.0     ┆ … ┆ null           ┆ null           ┆ ['Tereza Moc  ┆ 2024.0   │
│           ┆ 03:57:18   ┆ kráva          ┆           ┆   ┆                ┆                ┆ Watkinsová']  ┆          │
│ 9.7881e12 ┆ 2024-12-09 ┆ Adam Kašpar    ┆ 80.0      ┆ … ┆ null           ┆ null           ┆ ['Adam        ┆ 2023.0   │
│           ┆ 03:56:24   ┆                ┆           ┆   ┆                ┆                ┆ Kašpar',      ┆          │
│           ┆            ┆                ┆           ┆   ┆                ┆                ┆ 'Barbora      ┆          │
│           ┆            ┆                ┆           ┆   ┆                ┆                ┆ Kundr…        ┆          │
│ 9.7881e12 ┆ 2024-12-09 ┆ V šedi         ┆ 89.0      ┆ … ┆ null           ┆ 3.0            ┆ ['Milada      ┆ 2023.0   │
│           ┆ 03:42:10   ┆                ┆           ┆   ┆                ┆                ┆ Střítezská']  ┆          │
│ 9.7880e12 ┆ 2024-12-09 ┆ Příběhy tisíce ┆ 82.0      ┆ … ┆ 2.0            ┆ 7.0            ┆ ['Eduard      ┆ 2024.0   │
│           ┆ 03:56:43   ┆ a jedné noci   ┆           ┆   ┆                ┆                ┆ Petiška']     ┆          │
│ 9.7881e12 ┆ 2024-12-09 ┆ Pod křídly     ┆ 96.0      ┆ … ┆ null           ┆ 1.0            ┆ ['Ondřej      ┆ 2023.0   │
│           ┆ 03:41:38   ┆ Velkého        ┆           ┆   ┆                ┆                ┆ Pivoda']      ┆          │
│           ┆            ┆ krkavce        ┆           ┆   ┆                ┆                ┆               ┆          │
│ 9.7881e12 ┆ 2024-12-09 ┆ Muzikant na    ┆ 84.0      ┆ … ┆ 1.0            ┆ 2.0            ┆ ['Mirek       ┆ 2023.0   │
│           ┆ 03:41:49   ┆ jezeře         ┆           ┆   ┆                ┆                ┆ Vostrý']      ┆          │
│ 9.7881e12 ┆ 2024-12-09 ┆ Fake news a    ┆ 100.0     ┆ … ┆ null           ┆ 1.0            ┆ ['Ondřej      ┆ 2023.0   │
│           ┆ 03:50:49   ┆ politika       ┆           ┆   ┆                ┆                ┆ Vinař']       ┆          │
│           ┆            ┆ klasickéh…     ┆           ┆   ┆                ┆                ┆               ┆          │
│ 9.7880e12 ┆ 2024-09-23 ┆ Fotbalový sen  ┆ 94.0      ┆ … ┆ 1.0            ┆ null           ┆ null          ┆ null     │
│           ┆ 03:35:08   ┆                ┆           ┆   ┆                ┆                ┆               ┆          │
│ 9.7880e12 ┆ 2024-12-09 ┆ Pánevní dno a  ┆ 80.0      ┆ … ┆ null           ┆ null           ┆ ['Ida         ┆

In [240]:
df_gr = df_isbn.join(gr, left_on='isbn', right_on='GR_isbn',how='right')
df_gr.sample(10)

shape: (10, 88)
┌──────────┬──────────────────────┬────────────────┬───────────┬───┬────────────┬────────────┬──────────┬───────────┐
│ 100_ind1 ┆ 100_a                ┆ 100_7          ┆ 100_4     ┆ … ┆ GR_4_stars ┆ GR_5_stars ┆ GR_pages ┆ GR_format │
│ ---      ┆ ---                  ┆ ---            ┆ ---       ┆   ┆ ---        ┆ ---        ┆ ---      ┆ ---       │
│ str      ┆ str                  ┆ str            ┆ list[str] ┆   ┆ f64        ┆ f64        ┆ f64      ┆ str       │
╞══════════╪══════════════════════╪════════════════╪═══════════╪═══╪════════════╪════════════╪══════════╪═══════════╡
│ 1        ┆ Lauder, Silvie,      ┆ mzk2006324307  ┆ ["aut"]   ┆ … ┆ 107.0      ┆ 269.0      ┆ 400.0    ┆ paperback │
│ 1        ┆ Poláčková, Lenka     ┆ jo20221150966  ┆ ["aut"]   ┆ … ┆ 4.0        ┆ 2.0        ┆ 296.0    ┆ hardcover │
│ 1        ┆ Chalupa, Jiří,       ┆ jn19981000468  ┆ ["aut"]   ┆ … ┆ 0.0        ┆ 0.0        ┆ 768.0    ┆ hardcover │
│ 1        ┆ Sacká, Vlaďka,       ┆ xx0274874      ┆ ["aut"]   ┆ … ┆ 5.0        ┆ 1.0        ┆ 408.0    ┆ paperback │
│ 1        ┆ Stráníková, Jarmila, ┆ ola20211129086 ┆ ["aut"]   ┆ … ┆ 14.0       ┆ 11.0       ┆ 416.0    ┆ null      │
│ 1        ┆ Hrubý, Dan,          ┆ jn20000401090  ┆ ["aut"]   ┆ … ┆ 2.0        ┆ 0.0        ┆ 520.0    ┆ paperback │
│ 1        ┆ Landsman, Dominik,   ┆ jo2015854588   ┆ ["aut"]   ┆ … ┆ 0.0        ┆ 3.0        ┆ 224.0    ┆ hardcover │
│ 1        ┆ Kramerová, Daniela,  ┆ mzk2009495965  ┆ ["aut"]   ┆ … ┆ 0.0        ┆ 0.0        ┆ 200.0    ┆ paperback │
│ null     ┆ null                 ┆ null           ┆ null      ┆ … ┆ 0.0        ┆ 0.0        ┆ 151.0    ┆ paperback │
│ null     ┆ null                 ┆ null           ┆ null      ┆ … ┆ 17.0       ┆ 12.0       ┆ 472.0    ┆ hardcover │
└──────────┴──────────────────────┴────────────────┴───────────┴───┴────────────┴────────────┴──────────┴───────────┘

In [248]:
df_dk = df_isbn.join(dk.with_columns(pl.col('DK_isbn').cast(int).cast(str)), left_on='isbn', right_on='DK_isbn',how='right')

In [406]:
df_gr_graf = df_gr.filter(pl.col('GR_isbn').is_in(romany_isbn)).filter(pl.col("GR_rating") >= 0).filter(pl.col('GR_ratings_count') >= 5).filter(pl.col("stran") > 30)

In [418]:
gr_scatter = alt.Chart(
    alt_friendly(df_gr_graf),
    width=120
).mark_point(size=1, color='#81A9D5').encode(
    alt.X("stran:Q", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')),
    alt.Y("GR_rating:Q", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6'))
)

# Add regression line
gr_regression = alt.Chart(
    alt_friendly(df_gr_graf)
).transform_regression(
    'stran', 'GR_rating', method="linear"
).mark_line(color='#445B78').encode(
    alt.X("stran:Q", title="počet stran", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')),
    alt.Y("GR_rating:Q", title="hodnocení na Goodreads", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6'))
)

# Combine the plots
gr_final_chart = gr_scatter + gr_regression

gr_final_chart

alt.LayerChart(...)

In [402]:
df_dk_graf = df_dk.filter(pl.col('DK_isbn').is_in(romany_isbn)).filter(pl.col("DK_rating") >= 0).filter(pl.col('DK_ratings_count') >= 5).filter(pl.col("stran") > 30)

In [416]:
dk_scatter = alt.Chart(
    alt_friendly(df_dk_graf),

    width=120
).mark_point(size=1, color='#81A9D5').encode(
    alt.X("stran:Q"),
    alt.Y("DK_rating:Q")
)

# Add regression line
dk_regression = alt.Chart(
    alt_friendly(df_dk_graf)
).transform_regression(
    'stran', 'DK_rating'
).mark_line(color='#445B78').encode(
    alt.X("stran:Q", title="počet stran", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')),
    alt.Y("DK_rating:Q", title="hodnocení na Databázi knih", axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6'))
)

# Combine the plots
dk_final_chart = (dk_scatter + dk_regression)

dk_final_chart

alt.LayerChart(...)

In [412]:
len(df_gr_graf)

295

In [362]:
len(df_dk_graf)

616

In [420]:
alt.concat(gr_final_chart, dk_final_chart).properties(
    title=alt.Title("Dlouhé příběhy hodnotíme líp", subtitle=["Hodnocení českých románů z posledních let","na čtenářských platformách Goodreads a Databáze knih"])
)

alt.ConcatChart(...)